In [3]:
import geopandas as gpd
import pandas as pd
import numpy as np
import folium

In [6]:
df = pd.read_csv('../data/WildfireData.csv')
df.head()
# df.dtypes

Unnamed: 0  Unnamed: 0.1 fire_name  fire_size fire_size_class  \
0           0             0       NaN       10.0               C   
1           1             1       NaN        3.0               B   
2           2             2       NaN       60.0               C   
3           3             3    WNA  1        1.0               B   
4           4             4       NaN        2.0               B   

    stat_cause_descr   latitude   longitude state disc_clean_date  ...  \
0  Missing/Undefined  18.105072  -66.753044    PR       2/11/2007  ...   
1              Arson  35.038330  -87.610000    TN      12/11/2006  ...   
2              Arson  34.947800  -88.722500    MS       2/29/2004  ...   
3     Debris Burning  39.641400 -119.308300    NV        6/6/2005  ...   
4      Miscellaneous  30.700600  -90.591400    LA       9/22/1999  ...   

  Wind_cont Hum_pre_30 Hum_pre_15  Hum_pre_7   Hum_cont Prec_pre_30  \
0  3.250413  78.216590  76.793750  76.381579  78.724370         0.0   
1  2.122320  70.840000  65.858911  55.505882  81.682678        59.8   
2  3.369050  75.531629  75.868613  76.812834  65.063800       168.8   
3  0.000000  44.778429  37.140811  35.353846   0.000000        10.4   
4 -1.000000  -1.000000  -1.000000  -1.000000  -1.000000        -1.0   

   Prec_pre_15 Prec_pre_7 Prec_cont  remoteness  
0          0.0        0.0       0.0    0.017923  
1          8.4        0.0      86.8    0.184355  
2         42.2       18.1     124.5    0.194544  
3          7.2        0.0       0.0    0.487447  
4         -1.0       -1.0      -1.0    0.214633  

[5 rows x 43 columns]

In [7]:
df = df [['fire_size', 'latitude', 'longitude', 'state', 'stat_cause_descr']]
x = len(df)

In [8]:
df.head(15)

fire_size   latitude   longitude state   stat_cause_descr
0        10.0  18.105072  -66.753044    PR  Missing/Undefined
1         3.0  35.038330  -87.610000    TN              Arson
2        60.0  34.947800  -88.722500    MS              Arson
3         1.0  39.641400 -119.308300    NV     Debris Burning
4         2.0  30.700600  -90.591400    LA      Miscellaneous
5         1.0  32.063900  -82.417800    GA     Debris Burning
6         5.2  31.316978  -83.393649    GA     Debris Burning
7         1.0  30.904720  -93.557500    TX           Campfire
8         1.0  35.900310  -92.061180    AR              Arson
9         1.0  48.839400  -99.718500    ND      Miscellaneous
10        8.3  30.845339  -83.127987    GA     Debris Burning
11       37.0  31.195108  -88.150651    AL              Arson
12        1.0  33.855740  -85.311075    GA     Debris Burning
13        1.0  31.767380  -93.146870    LA          Fireworks
14        3.0  32.775000  -80.658333    SC  Missing/Undefined

In [9]:
df = df.loc[df['fire_size'] > 1000]

In [ ]:
m = folium.Map(location = [37.256500, -122.027153],
               zoom_start = 6.5)

small_wildfires = folium.FeatureGroup(name = '< 10000 Acres')
medium_wildfires = folium.FeatureGroup(name = '10,000 - 50,000 Acres')
large_wildfires = folium.FeatureGroup(name = '50,000 - 100,000 Acres')
xl_wildfires = folium.FeatureGroup(name = '> 100,000 Acres')
lightning = folium.FeatureGroup(name = 'Lightning')
arson = folium.FeatureGroup(name = 'Arson')
miscellaneous = folium.FeatureGroup(name = 'Miscellaneous')



for i, v in df.iterrows():
    fire_size = float(v['fire_size'])
    state = str(v['state'])
    cause = str(v['stat_cause_descr'])
    
    popup = """
    Size (Acres) : <b>%s</b><br>
    State : <b>%s</b><br>
    Cause : <b>%s</b><br>
    """ % (v['fire_size'], v['state'], v['stat_cause_descr'])
    
    
    if fire_size < 10000:
        folium.CircleMarker(location = [v['latitude'], v['longitude']],
                           radius = np.log(fire_size) * 0.8,
                           weight = 0,
                           tooltip = popup,
                           color = '#ffeda0',
                           fill_color = '#ffeda0',
                           fill_opacity = 0.7,
                           fill = True).add_to(small_wildfires)
        
    if fire_size in range(10000, 50000):
        folium.CircleMarker(location = [v['latitude'], v['longitude']],
                           radius = np.log(fire_size),
                           weight = 0,
                           tooltip = popup,
                           color = '#feb24c',
                           fill_color = '#feb24c',
                           fill_opacity = 0.7,
                           fill = True).add_to(medium_wildfires)
    
    if fire_size in range(50000, 100000):
        folium.CircleMarker(location = [v['latitude'], v['longitude']],
                           radius = np.log(fire_size) * 1.5,
                           weight = 0,
                           tooltip = popup,
                           color = '#fc4e2a',
                           fill_color = '#fc4e2a',
                           fill_opacity = 0.7,
                           fill = True).add_to(large_wildfires)

    if fire_size > 100000:
        folium.CircleMarker(location = [v['latitude'], v['longitude']],
                           radius = np.log(fire_size) * 2,
                           weight = 0,
                           tooltip = popup,
                           color = '#b10026',
                           fill_color = '#b10026',
                           fill_opacity = 0.7,
                           fill = True).add_to(xl_wildfires)

small_wildfires.add_to(m)
medium_wildfires.add_to(m)
large_wildfires.add_to(m)
xl_wildfires.add_to(m)
folium.LayerControl(collapsed = False).add_to(m)

m.save(r'../templates/visualize-map.html')
m

In [13]:
m2 = folium.Map(location = [37.256500, -122.027153],
               zoom_start = 6.5)

lightning = folium.FeatureGroup(name = 'Lightning')
arson = folium.FeatureGroup(name = 'Arson')
debris = folium.FeatureGroup(name = 'Debris Burning')
equipment = folium.FeatureGroup(name = 'Equipment Use')
other = folium.FeatureGroup(name= "Other")



for i, v in df.iterrows():
    fire_size = float(v['fire_size'])
    state = str(v['state'])
    cause = str(v['stat_cause_descr'])
    
    popup = """
    Size (Acres) : <b>%s</b><br>
    State : <b>%s</b><br>
    Cause : <b>%s</b><br>
    """ % (v['fire_size'], v['state'], v['stat_cause_descr'])
    
    
    if cause == "Lightning":
        folium.CircleMarker(location = [v['latitude'], v['longitude']],
                           radius = np.log(fire_size) * 1.5,
                           weight = 0,
                           tooltip = popup,
                           color = '#0000FF',
                           fill_color = '#0000FF',
                           fill_opacity = 0.7,
                           fill = True).add_to(lightning)
        
    
    elif cause == "Arson":
        folium.CircleMarker(location = [v['latitude'], v['longitude']],
                           radius = np.log(fire_size) * 1.5,
                           weight = 0,
                           tooltip = popup,
                           color = '#b10026',
                           fill_color = '#b10026',
                           fill_opacity = 0.7,
                           fill = True).add_to(arson)

    elif cause == "Debris Burning":
         folium.CircleMarker(location = [v['latitude'], v['longitude']],
                           radius = np.log(fire_size) * 1.5,
                           weight = 0,
                           tooltip = popup,
                           color = '#e534eb',
                           fill_color = '#e534eb',
                           fill_opacity = 0.7,
                           fill = True).add_to(debris)

    elif cause == "Equipment Use":
         folium.CircleMarker(location = [v['latitude'], v['longitude']],
                           radius = np.log(fire_size) * 1.5,
                           weight = 0,
                           tooltip = popup,
                           color = '#747eed',
                           fill_color = '#747eed',
                           fill_opacity = 0.7,
                           fill = True).add_to(equipment)

    else: 
        folium.CircleMarker(location = [v['latitude'], v['longitude']],
                           radius = np.log(fire_size) * 1.5,
                           weight = 0,
                           tooltip = popup,
                           color = '#32a852',
                           fill_color = '#32a852',
                           fill_opacity = 0.7,
                           fill = True).add_to(other)

arson.add_to(m2)
other.add_to(m2)
debris.add_to(m2)
equipment.add_to(m2)
lightning.add_to(m2)

folium.LayerControl(collapsed = False).add_to(m2)
m2.save(r'../templates/visualize-map2.html')
m2